In [ ]:
%matplotlib inline


# Neural Style Transfer with ``pystiche``

This example showcases how a basic Neural Style Transfer (NST), i.e. image
optimization, could be performed with ``pystiche``.

<div class="alert alert-info"><h4>Note</h4><p>This is an *example how to implement an NST* and **not** a
    *tutorial on how NST works*. As such, it will not explain why a specific choice was
    made or how a component works. If you have never worked with NST before, we
    **strongly** suggest you to read the `gist` first.</p></div>



## Setup

We start this example by importing everything we need and setting the device we will
be working on.



In [ ]:
import pystiche
from pystiche import demo, enc, loss, optim
from pystiche.image import show_image
from pystiche.misc import get_device, get_input_image

print(f"I'm working with pystiche=={pystiche.__version__}")

device = get_device()
print(f"I'm working with {device}")

## Multi-layer Encoder
The ``content_loss`` and the ``style_loss`` operate on the encodings of an image
rather than on the image itself. These encodings are generated by a pretrained
encoder. Since we will be using encodings from multiple layers we load a
multi-layer encoder. In this example we use the
:func:`~pystiche.enc.vgg19_multi_layer_encoder` that is based on the VGG19
architecture introduced by Simonyan and Zisserman :cite:`SZ2014` .



In [ ]:
multi_layer_encoder = enc.vgg19_multi_layer_encoder()
print(multi_layer_encoder)

## Perceptual Loss

The core components of every NST are the ``content_loss`` and the ``style_loss``.
Combined they make up the perceptual loss, i.e. the optimization criterion.

In this example we use the :class:`~pystiche.loss.FeatureReconstructionLoss`
introduced by Mahendran and Vedaldi :cite:`MV2015` as ``content_loss``. We first
extract the ``content_encoder`` that generates encodings from the ``content_layer``.
Together with the ``content_weight`` we can construct the ``content_loss``.



In [ ]:
content_layer = "relu4_2"
content_encoder = multi_layer_encoder.extract_encoder(content_layer)
content_weight = 1e0
content_loss = loss.FeatureReconstructionLoss(
    content_encoder, score_weight=content_weight
)
print(content_loss)

We use the :class:`~pystiche.loss.GramLoss` introduced by Gatys, Ecker, and Bethge
:cite:`GEB2016` as ``style_loss``. Unlike before, we use multiple ``style_layers``.
The individual losses can be conveniently bundled in a
:class:`~pystiche.loss.MultiLayerEncodingLoss`.



In [ ]:
style_layers = ("relu1_1", "relu2_1", "relu3_1", "relu4_1", "relu5_1")
style_weight = 1e3


def get_style_op(encoder, layer_weight):
    return loss.GramLoss(encoder, score_weight=layer_weight)


style_loss = loss.MultiLayerEncodingLoss(
    multi_layer_encoder, style_layers, get_style_op, score_weight=style_weight,
)
print(style_loss)

We combine the ``content_loss`` and ``style_loss`` into a joined
:class:`~pystiche.loss.PerceptualLoss`, which will serve as optimization criterion.



In [ ]:
perceptual_loss = loss.PerceptualLoss(content_loss, style_loss).to(device)
print(perceptual_loss)

## Images

We now load and show the images that will be used in the NST. The images will be
resized to ``size=500`` pixels.



In [ ]:
images = demo.images()
images.download()
size = 500

<div class="alert alert-info"><h4>Note</h4><p>``ìmages.download()`` downloads **all** demo images upfront. If you only want to
  download the images for this example remove this line. They will be downloaded at
  runtime instead.</p></div>

<div class="alert alert-info"><h4>Note</h4><p>If you want to work with other images you can load them with
  :func:`~pystiche.image.read_image`:

  .. code-block:: python

    from pystiche.image import read_image

    my_image = read_image("my_image.jpg", size=size, device=device)</p></div>



In [ ]:
content_image = images["bird1"].read(size=size, device=device)
show_image(content_image, title="Content image")

In [ ]:
style_image = images["paint"].read(size=size, device=device)
show_image(style_image, title="Style image")

## Neural Style Transfer

After loading the images they need to be set as targets for the optimization
``criterion``.



In [ ]:
perceptual_loss.set_content_image(content_image)
perceptual_loss.set_style_image(style_image)

As a last preliminary step we create the input image. We start from the
``content_image`` since this way the NST converges quickly.



In [ ]:
starting_point = "content"
input_image = get_input_image(starting_point, content_image=content_image)
show_image(input_image, title="Input image")

<div class="alert alert-info"><h4>Note</h4><p>If you want to start from a white noise image instead use
  ``starting_point = "random"`` instead:

  .. code-block:: python

    starting_point = "random"
    input_image = get_input_image(starting_point, content_image=content_image)</p></div>



Finally we run the NST with the :func:`~pystiche.optim.image_optimization` for
``num_steps=500`` steps.

In every step the ``perceptual_loss`` is calculated nd propagated backward to the
pixels of the ``input_image``. If ``get_optimizer`` is not specified, as is the case
here, the :func:`~pystiche.optim.default_image_optimizer`, i.e.
:class:`~torch.optim.LBFGS` is used.



In [ ]:
output_image = optim.image_optimization(input_image, perceptual_loss, num_steps=500)

After the NST is complete we show the result.



In [ ]:
show_image(output_image, title="Output image")

## Conclusion

If you started with the basic NST example without ``pystiche`` this example hopefully
convinced you that ``pystiche`` is a helpful tool. But this was just the beginning:
to unleash its full potential head over to the more advanced examples.

